In [4]:
from datascience import *
from datascience.predicates import are
path_data = '../../../../data/'
import numpy as np
import matplotlib
matplotlib.use('Agg')
%matplotlib inline
import matplotlib.pyplot as plots
plots.style.use('fivethirtyeight')
import warnings
warnings.simplefilter(action="ignore", category=FutureWarning)
from bancor_research import Decimal
import pandas as pd
from urllib.request import urlopen
import re

from bancor_research.bancor_simulator.v3.spec.network import *

# Recall from an earlier chapter that we already defined the whitelisted_tokens as follows.
cooldown_time: int = 7
iter_limit = 10000
bnt_min_liquidity: Decimal = Decimal('10000')
bnt_funding_limit: Decimal = Decimal('40000')
whitelisted_tokens: list = ['bnt', 'eth', 'wbtc', 'link']

withdrawal_fee: Decimal = Decimal('0.0025')
price_feeds = pd.DataFrame({'INDX':[0 for i in range(iter_limit + 1)],
                            'bnt':[2.5 for i in range(iter_limit + 1)],
                            'link':[15.00 for i in range(iter_limit + 1)],
                            'eth':[2500.00 for i in range(iter_limit + 1)],
                            'wbtc':[40000.00 for i in range(iter_limit + 1)]})

network_fee: Decimal = Decimal('0.2')
trading_fee: Decimal = Decimal('0.01')

# There are other possible configuration settings available, however for the present purpose we will use the defaults.
v3 = BancorDapp(whitelisted_tokens=whitelisted_tokens,
              network_fee=network_fee,
              trading_fee=trading_fee,
              cooldown_time=cooldown_time,
              withdrawal_fee=withdrawal_fee,
              bnt_min_liquidity=bnt_min_liquidity,
              bnt_funding_limit=bnt_funding_limit,
              price_feeds=price_feeds)

v3.create_user('Alice')
v3.create_user('Bob')
v3.create_user('Charlie')

v3.set_user_balance(user_name='Alice', tkn_name='eth', tkn_amt=101)
v3.set_user_balance(user_name='Charlie', tkn_name='link', tkn_amt=10001)
v3.set_user_balance(user_name='Bob', tkn_name='wbtc', tkn_amt=101)

# The actual deposits.

v3.deposit(tkn_amt=100, tkn_name='eth', user_name='Alice')

v3.deposit(tkn_amt=10000, tkn_name='link', user_name='Charlie')

v3.deposit(tkn_amt=100, tkn_name='wbtc', user_name='Bob')

v3.deposit(tkn_amt=1, tkn_name='eth', user_name='Alice')

v3.deposit(tkn_amt=1, tkn_name='link', user_name='Charlie')

v3.deposit(tkn_amt=1, tkn_name='wbtc', user_name='Bob')

v3.dao_msig_init_pools(whitelisted_tokens, 'bnt')

v3.set_user_balance(user_name='Trader', tkn_name='bnt', tkn_amt=2000)

v3.trade(tkn_amt=2000, source_token='bnt',  target_token='link', user_name='Trader', timestamp=0)

def read_url(url): 
    return re.sub('\\s+', ' ', urlopen(url).read().decode())

Bootstrap requirements met for eth
Bootstrap requirements met for wbtc
Bootstrap requirements met for link


In [5]:
v3.describe()

bnt  \
Account  Alice                                          NaN   
         Bob                                            NaN   
         Charlie                                        NaN   
         Trader                                       0E-18   
Contract EP Vault                                         0   
         ER Vault                                         0   
         Master Vault              62000.000000000000000000   
         Protocol                                       NaN   
Pool     a: TKN Staked Balance                          NaN   
         b: TKN Trading Liquidity                       NaN   
         c: BNT Trading Liquidity                       NaN   
         d: BNT Current Funding                         NaN   
         e: Spot Rate                                   NaN   
         f: Average Rate                                NaN   
         g: Average Inverse Rate                        NaN   

                                                        eth  \
Account  Alice                                        0E-18   
         Bob                                            NaN   
         Charlie                                        NaN   
         Trader                                         NaN   
Contract EP Vault                                         0   
         ER Vault                                         0   
         Master Vault                101.000000000000000000   
         Protocol                                       NaN   
Pool     a: TKN Staked Balance       101.000000000000000000   
         b: TKN Trading Liquidity     20.000000000000000000   
         c: BNT Trading Liquidity  20000.000000000000000000   
         d: BNT Current Funding    20000.000000000000000000   
         e: Spot Rate                                  1E+3   
         f: Average Rate                               1E+3   
         g: Average Inverse Rate                          0   

                                                       wbtc  \
Account  Alice                                          NaN   
         Bob                                          0E-18   
         Charlie                                        NaN   
         Trader                                         NaN   
Contract EP Vault                                         0   
         ER Vault                                         0   
         Master Vault                101.000000000000000000   
         Protocol                                       NaN   
Pool     a: TKN Staked Balance       101.000000000000000000   
         b: TKN Trading Liquidity      1.250000000000000000   
         c: BNT Trading Liquidity  20000.000000000000000000   
         d: BNT Current Funding    20000.000000000000000000   
         e: Spot Rate                                1.6E+4   
         f: Average Rate                             1.6E+4   
         g: Average Inverse Rate                          0   

                                                            link  \
Account  Alice                                               NaN   
         Bob                                                 NaN   
         Charlie                                           0E-18   
         Trader                           300.000000000000000000   
Contract EP Vault                                              0   
         ER Vault                                              0   
         Master Vault                    9701.000000000000000000   
         Protocol                                            NaN   
Pool     a: TKN Staked Balance          10003.424242424242424242   
         b: TKN Trading Liquidity        3033.333333333333333333   
         c: BNT Trading Liquidity       21995.604395604395604396   
         d: BNT Current Funding         20000.000000000000000000   
         e: Spot Rate              7.251298152397053495955522121   
         f: Average Rate           6.000000000000000000000000000   
         

# Trading and Fees - TKN to BNT

Assume now that a trader wants to perform the opposite action, perhaps to close an arbitrage opportunity left open by the previous swap. The trader sends 302.9981 LINK into the vault, and the vault sends 1977.6155 BNT to the trader. As before, the trader’s intuition agrees with the changing state of the vault balances; however, the changes in the trading liquidity and staked balances require closer examination.

In [6]:
v3.trade(tkn_amt=302.9981, source_token='link',  target_token='bnt', user_name='Trader', timestamp=0)

v3.describe(decimals=4)

bnt         eth        wbtc  \
Account  Alice                            NaN      0.0000         NaN   
         Bob                              NaN         NaN      0.0000   
         Charlie                          NaN         NaN         NaN   
         Trader                     1977.6153         NaN         NaN   
Contract EP Vault                      0.0000      0.0000      0.0000   
         ER Vault                      0.0000      0.0000      0.0000   
         Master Vault              60022.3847    101.0000    101.0000   
         Protocol                         NaN         NaN         NaN   
Pool     a: TKN Staked Balance            NaN    101.0000    101.0000   
         b: TKN Trading Liquidity         NaN     20.0000      1.2500   
         c: BNT Trading Liquidity         NaN  20000.0000  20000.0000   
         d: BNT Current Funding           NaN  20000.0000  20000.0000   
         e: Spot Rate                     NaN   1000.0000  16000.0000   
         f: Average Rate                  NaN   1000.0000  16000.0000   
         g: Average Inverse Rate          NaN      0.0000      0.0000   

                                         link       bnbnt     bneth    bnwbtc  \
Account  Alice                            NaN         NaN  101.0000       NaN   
         Bob                              NaN         NaN       NaN  101.0000   
         Charlie                       0.0000         NaN       NaN       NaN   
         Trader                       -2.9981         NaN       NaN       NaN   
Contract EP Vault                      0.0000         NaN       NaN       NaN   
         ER Vault                      0.0000         NaN       NaN       NaN   
         Master Vault              10003.9981         NaN       NaN       NaN   
         Protocol                         NaN  60000.0000    0.0000    0.0000   
Pool     a: TKN Staked Balance     10003.4242         NaN       NaN       NaN   
         b: TKN Trading Liquidity   3336.3314         NaN       NaN       NaN   
         c: BNT Trading Liquidity  20013.9939         NaN       NaN       NaN   
         d: BNT Current Funding    20015.9807         NaN       NaN       NaN   
         e: Spot Rate                  5.9988         NaN       NaN       NaN   
         f: Average Rate               6.0000         NaN       NaN       NaN   
         g: Average Inverse Rate       0.0000         NaN       NaN       NaN   

                                       bnlink  
Account  Alice                            NaN  
         Bob                              NaN  
         Charlie                   10001.0000  
         Trader                           NaN  
Contract EP Vault                         NaN  
         ER Vault                         NaN  
         Master Vault                     NaN  
         Protocol                      0.0000  
Pool     a: TKN Staked Balance            NaN  
         b: TKN Trading Liquidity         NaN  
         c: BNT Trading Liquidity         NaN  
         d: BNT Current Funding           NaN  
         e: Spot Rate                     NaN  
         f: Average Rate                  NaN  
         g: Average Inverse Rate          NaN

In this trade, the target asset is BNT. Therefore, there is no need to perform a second, virtual swap at the end of the trade. Instead, the vortex fee is taken directly from the effective fee. Importantly, this results in a slightly reduced change in the growth of the BNT trading liquidity as judged from the trader's perspective. The trader's fee totals 19.9759 BNT, of which 3.9952 BNT becomes the property of the Bancor Vortex. The difference (15.9807 BNT) is added to the BNT staking ledger, and causes the value of the bnBNT pool token to appreciate.

Therefore, during the trade the following components of the system were changed:

1. The vault balances. The change in the vault is always in agreement with the trader's intuition. In this case, the trader sent 302.99814 LINK into the vault, and received 1977.615545 BNT from it. Therefore, the vault balance of LINK necessarily increased by 302.99814 LINK, and decreased by 1977.615545 BNT.

2. The staking ledger. Trading fees are always taken from the target asset. Therefore, the value of the bnBNT pool token must be appreciated by 80% of the fee apparent to the trader (i.e. the total fee - vortex rate). A total of 15.980731 BNT tokens are added to the staked amount, which becomes the property of the bnBNT pool token holders (at this point in the narrative, is the protocol only).

3. The vortex ledger. A portion of the fee paid by the trader is effectively collected, and added to the vortex ledger.

4. The trading liquidity. The apparent disagreement between the intuitive result, and the one obtained, is accounted for by the effect of the BNT collection by the vortex.

The change in the BNT and LINK trading liquidity can be expressed as follows:

![](https://lh3.googleusercontent.com/fdNz0QqFKQ0CaabnT7t8pfphTCylaW4ox8YEPNF_i662Xgt3CECetm3GRt34YJ5orHz2zXPPRNX6uIPOlLX1PwSjCXaWmCCcAYrpaeTS0gip1FGZTjOlcOqOACtUJAm-dtXGtsVH)

![](https://lh6.googleusercontent.com/femAV9RrDUJnonpzPV4mevFeQYL1F5RkUXktaroDl78ixkfTwxssW0mglLr0eS_KvC6l0ZewOMX0oQKmi-cnXRpe69q9wg3xich5UXF46qbXEPP9pRzN1xZ94I_dmXnoPRVX2vS1)

![](https://lh6.googleusercontent.com/Y5Isbbj4UjPyamIcti-mUZNAjYiopquxluK2rM0AXAkpqP6ZYhpTU9Ad447Z334-q5b_a2yXXp5oSCBf7e_a3ZqmpG_O9xU3SPfSOtAK8vwOW9cOWBe4VL0bWDFOFzN9k-sd7Veh)

where a1† and a1 are the BNT trading liquidity balances of the pool after and before the trade, respectively, b1† and b1 are the LINK trading liquidity balances of the pool after and before the trade, respectively, d1 is the pool fee (e.g. 0.01, or 1%) and e is the Vortex rate (e.g. 0.2, or 20%). The number of LINK tokens being sent into the vault is x, and the number of BNT tokens sent back to the trader is bntOut. The change in the TKN trading liquidity (and therefore the update to the available LINK trading liquidity) is unchanged from the standard case. The calculation of the fee awarded to liquidity providers, denominated in BNT and added to the staking ledger is:

![](https://lh4.googleusercontent.com/L37q1CVjSJ4-I_j8q_cdhXbxgP9oZ7PXkJ3UVzH67xmPyj9fHUucHYQVBt6wkDnYidSawiK4BIFDbLf1exJc_p7PEDPBgim4XAHRLtBk9IaGCvblhyAXfxnYAk0EcAsJ_CGx_ai_)

And the calculation for the fee given to the Bancor Vortex, denominated exclusively in BNT and added to the vortex ledger is:

![](https://lh3.googleusercontent.com/0sr_cE39asE2B1XQGhuD3whJwUP_yhjwv3QswhtG-nPmfTLQGFBgScf8HAtEyWnGiapYkaTkc5qhdCW0DlZzHDJTRWaTFtYB3Ynn2uij2Tga0czOs-gHFMii521VkSNlLk7KsPDf)